In [60]:
from torch import nn
import numpy as np
import torch
import os

class CNN3D(nn.Module):
    def __init__(self, hidden_size=32, dropout=0.0):
        super(CNN3D, self).__init__()
        self.conv1 = nn.Conv3d(1, hidden_size, kernel_size=3, stride=1, padding=1)
        self.batchnorm = nn.BatchNorm3d(hidden_size)
        self.conv2 = nn.Conv3d(hidden_size, hidden_size*2, kernel_size=3, stride=1, padding=1)
        self.relu = nn.ReLU()
        self.maxpool = nn.MaxPool3d(kernel_size=2, stride=2)
        self.fc1 = nn.Linear(hidden_size*32, 256)  # Calculate input size based on output from conv3
        self.fc2 = nn.Linear(256, 6)
        self.dropout = nn.Dropout(dropout)

    def forward(self, x):
        x = self.conv1(x)
        x = self.relu(x)
        x = self.maxpool(x)
        x = self.batchnorm(x)
        x = self.conv2(x)
        x = self.relu(x)
        x = self.maxpool(x)
        x = self.dropout(x)

        x = x.view(x.size(0), -1)  # Flatten features for fully connected layers
        x = self.fc1(x)
        x = self.relu(x)
        x = self.fc2(x)
        return x

def train(model, criterion, optimizer, loader, epochs=5):
    for epoch in range(epochs):
        for idx, (inputs, labels) in enumerate(loader):
            optimizer.zero_grad()
            outputs = model(inputs)
            loss = criterion(outputs, labels)
            loss.backward()
            optimizer.step()
        # print(f'Epoch {epoch}, Loss: {loss.item()}')
    return model




class Model():
    def __init__(self, batch_size=8,lr=0.001,epochs=10, dropout=0.0, hidden_size=32):
        self.batch_size = batch_size
        self.lr = lr
        self.epochs = epochs
        self.model = CNN3D(dropout=dropout, hidden_size=hidden_size)
        self.criterion = nn.CrossEntropyLoss()
        self.optimizer = torch.optim.Adam(self.model.parameters(), lr=self.lr)

    def fit(self, X, y):
        X, y = self.process_data(X, y)
        train_dataset = torch.utils.data.TensorDataset(X, y)
        train_loader = torch.utils.data.DataLoader(train_dataset, batch_size=self.batch_size, shuffle=True)
        train(self.model, self.criterion, self.optimizer, train_loader, self.epochs)

    def predict(self, X):
        self.model.eval()
        with torch.no_grad():
            X = np.array([video[:6] for video in X])
            tensor_videos = torch.tensor(X, dtype=torch.float32)
            # Clip values to 0 and 255
            tensor_videos = np.clip(tensor_videos, 0, 255)
            # Replace NaNs in each frame, with the average of the frame. This was generated with GPT
            for i in range(tensor_videos.shape[0]):
                for j in range(tensor_videos.shape[1]):
                    tensor_videos[i][j][torch.isnan(tensor_videos[i][j])] = torch.mean(
                        tensor_videos[i][j][~torch.isnan(tensor_videos[i][j])])
            X = torch.Tensor(tensor_videos.unsqueeze(1))
            result = self.model(X)
        return torch.max(result, dim=1)[1].numpy()
    def process_data(self, X, y, n_samples=600):
        y = np.array(y)
        X = np.array([video[:6] for video in X])
        tensor_videos = torch.tensor(X, dtype=torch.float32)
        # Clip values to 0 and 255
        tensor_videos = np.clip(tensor_videos, 0, 255)
        # Replace NaNs in each frame, with the average of the frame. This was generated with GPT
        for i in range(tensor_videos.shape[0]):
            for j in range(tensor_videos.shape[1]):
                tensor_videos[i][j][torch.isnan(tensor_videos[i][j])] = torch.mean(
                    tensor_videos[i][j][~torch.isnan(tensor_videos[i][j])])
        # Undersample the data for each of the 6 classes. Select max of 300 samples for each class
        # Very much generated with the assitance of chatGPT with some modifications
        # Get the indices of each class
        indices = [np.argwhere(y == i).squeeze(1) for i in range(6)]
        # Get the number of samples to take for each class
        # Get the indices of the samples to take
        indices_to_take = [np.random.choice(indices[i], n_samples, replace=True) for i in range(6)]
        # Concatenate the indices
        indices_to_take = np.concatenate(indices_to_take)
        # Select the samples
        tensor_videos = tensor_videos[indices_to_take].unsqueeze(1)
        y = y[indices_to_take]
        return torch.Tensor(tensor_videos), torch.Tensor(y).long()


In [27]:
from sklearn.metrics import f1_score
import optuna
from sklearn.model_selection import train_test_split

with open('data.npy', 'rb') as f:
    data = np.load(f, allow_pickle=True).item()
    X = data['data']
    y = data['label']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.1, random_state=1)

not_nan_indices = np.argwhere(~np.isnan(np.array(y_test))).squeeze()
y_test = [y_test[i] for i in not_nan_indices]
X_test = [X_test[i] for i in not_nan_indices]


def objective(trial):
    batch = trial.suggest_int("batch_size", 1, 12, log=True)
    epochs = trial.suggest_int("epochs", 1, 20)
    model = Model(batch_size=2**batch, epochs=epochs)
    model.fit(X_train, y_train)
    pred = model.predict(X_test)
    return -f1_score(y_test, pred, average='macro')
# Run optimization
# storage = optuna.storages.InMemoryStorage()
# study = optuna.create_study(storage=storage)
# study.optimize(objective, n_trials=10)
# 
# best_score = study.best_value
# best_params = study.best_params
# 
# print(best_score, best_params)

In [17]:
for i in range(3):
    model = Model(batch_size=8, epochs=10)
    model.fit(X_train, y_train)
    pred = model.predict(X_test)
    print(f1_score(y_test, pred, average='macro'))

KeyboardInterrupt: 

In [19]:
# Study of best learning rate
def objective(trial):
    lr = trial.suggest_float("lr", 1e-5, 5e-1, log=True)
    model = Model(lr=lr)
    model.fit(X_train, y_train)
    pred = model.predict(X_test)
    return -f1_score(y_test, pred, average='macro')
study = optuna.create_study(storage=storage, study_name="Learning_rate")
study.optimize(objective, n_trials=10)


DuplicatedStudyError: 

In [24]:
for i in range(3):
    model = Model()
    model.fit(X_train, y_train)
    pred = model.predict(X_test)
    print(f1_score(y_test, pred, average='macro'))
# WIth LR 0.00016764273108300424

0.6912320650364129
0.6607744107744108
0.6665432155087326


In [25]:
for i in range(3):
    model = Model(lr=0.001)
    model.fit(X_train, y_train)
    pred = model.predict(X_test)
    print(f1_score(y_test, pred, average='macro'))

0.706415970280129
0.7055600716120302
0.67676009342676


In [35]:
def objective(trial):
    dropout = trial.suggest_float("dropout", 0.0, 0.5, step=0.1)
    model = Model(dropout=dropout, lr=0.001)
    model.fit(X_train, y_train)
    pred = model.predict(X_test)
    return -f1_score(y_test, pred, average='macro')
study = optuna.create_study(storage=storage, study_name="dropout")
study.optimize(objective, n_trials=10)

study.best_params, study.best_value

[I 2024-04-28 13:38:45,580] A new study created in memory with name: dropout
[I 2024-04-28 13:39:09,602] Trial 0 finished with value: -0.5916579614840399 and parameters: {'dropout': 0.2}. Best is trial 0 with value: -0.5916579614840399.
[I 2024-04-28 13:39:33,716] Trial 1 finished with value: -0.706054567707244 and parameters: {'dropout': 0.5}. Best is trial 1 with value: -0.706054567707244.
[I 2024-04-28 13:39:58,041] Trial 2 finished with value: -0.6914798955557488 and parameters: {'dropout': 0.1}. Best is trial 1 with value: -0.706054567707244.
[I 2024-04-28 13:40:22,578] Trial 3 finished with value: -0.7369303922613968 and parameters: {'dropout': 0.1}. Best is trial 3 with value: -0.7369303922613968.
[I 2024-04-28 13:40:46,740] Trial 4 finished with value: -0.7529025381898083 and parameters: {'dropout': 0.4}. Best is trial 4 with value: -0.7529025381898083.
[I 2024-04-28 13:41:10,786] Trial 5 finished with value: -0.6720344567712989 and parameters: {'dropout': 0.30000000000000004}.

({'dropout': 0.4}, -0.7529025381898083)

In [37]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.1)
not_nan_indices = np.argwhere(~np.isnan(np.array(y_test))).squeeze()
y_test = [y_test[i] for i in not_nan_indices]
X_test = [X_test[i] for i in not_nan_indices]

for i in range(3):
    model = Model(dropout=0.4, lr=0.001)
    model.fit(X_train, y_train)
    pred = model.predict(X_test)
    print(f1_score(y_test, pred, average='macro'))


0.6141327807994474
0.6064872820918911
0.6300338376466196


In [38]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.1)
not_nan_indices = np.argwhere(~np.isnan(np.array(y_test))).squeeze()
y_test = [y_test[i] for i in not_nan_indices]
X_test = [X_test[i] for i in not_nan_indices]

for i in range(3):
    model = Model(dropout=0.1, lr=0.001)
    model.fit(X_train, y_train)
    pred = model.predict(X_test)
    print(f1_score(y_test, pred, average='macro'))

0.6413423296891699
0.6768407575558187
0.6221822007289135


In [39]:
for i in range(3):
    model = Model(dropout=0.0, lr=0.001)
    model.fit(X_train, y_train)
    pred = model.predict(X_test)
    print(f1_score(y_test, pred, average='macro'))

0.6933099871956078
0.662550713257427
0.7479965052551641


In [51]:
def objective(trial):
    hidden_layer = trial.suggest_int("hidden_layer", 0, 6, step=1)
    model = Model(hidden_size=2**hidden_layer)
    model.fit(X_train, y_train)
    pred = model.predict(X_test)
    return -f1_score(y_test, pred, average='macro')
study = optuna.create_study(storage=storage, study_name="hidden_layer")
study.optimize(objective, n_trials=10)


[I 2024-04-28 13:54:45,435] A new study created in memory with name: hidden_layer
[I 2024-04-28 13:55:08,688] Trial 0 finished with value: -0.6744674992735161 and parameters: {'hidden_layer': 5}. Best is trial 0 with value: -0.6744674992735161.
[I 2024-04-28 13:55:17,295] Trial 1 finished with value: -0.28941963054866277 and parameters: {'hidden_layer': 0}. Best is trial 0 with value: -0.6744674992735161.
[I 2024-04-28 13:55:27,158] Trial 2 finished with value: -0.5233606132063355 and parameters: {'hidden_layer': 1}. Best is trial 0 with value: -0.6744674992735161.
[I 2024-04-28 13:56:19,013] Trial 3 finished with value: -0.6249650240541486 and parameters: {'hidden_layer': 6}. Best is trial 0 with value: -0.6744674992735161.
[I 2024-04-28 13:57:10,821] Trial 4 finished with value: -0.7192056747499614 and parameters: {'hidden_layer': 6}. Best is trial 4 with value: -0.7192056747499614.
[I 2024-04-28 13:57:21,125] Trial 5 finished with value: -0.49548899023401516 and parameters: {'hidden

In [52]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.1)
not_nan_indices = np.argwhere(~np.isnan(np.array(y_test))).squeeze()
y_test = [y_test[i] for i in not_nan_indices]
X_test = [X_test[i] for i in not_nan_indices]
for i in range(3):
    model = Model(hidden_size=32)
    model.fit(X_train, y_train)
    pred = model.predict(X_test)
    print("size: 32", f1_score(y_test, pred, average='macro'))
for i in range(3):
    model = Model(hidden_size=16)
    model.fit(X_train, y_train)
    pred = model.predict(X_test)
    print("size: 16", f1_score(y_test, pred, average='macro'))
    
for i in range(3):
    model = Model(hidden_size=64)
    model.fit(X_train, y_train)
    pred = model.predict(X_test)
    print("size: 64", f1_score(y_test, pred, average='macro'))


size: 32 0.7587148200217135
size: 32 0.7007023098468655
size: 32 0.703371572957317
size: 16 0.6527439030663686
size: 16 0.6701033952446381
size: 16 0.6303813565416863
size: 64 0.6967700946646325
size: 64 0.6868739609967679
size: 64 0.7137992158825491


In [61]:
for i in range(3):
    model = Model(batch_size=64, epochs=20, lr=0.005)
    model.fit(X_train, y_train)
    pred = model.predict(X_test)
    print("1->8->16", f1_score(y_test, pred, average='macro'))


1->8->16 0.6983043227229274
1->8->16 0.6151284777600567
1->8->16 0.5974537037037037


In [62]:
for i in range(3):
    model = Model()
    model.fit(X_train, y_train)
    pred = model.predict(X_test)
    print("1->8->16", f1_score(y_test, pred, average='macro'))


1->8->16 0.655143327874276
1->8->16 0.6882410205760642
1->8->16 0.7252563893010118
